In [1]:
import numpy as np
import pandas as pd
from pandas.tseries.offsets import Hour, Minute
from pandas.tseries.offsets import Day, MonthEnd
from pandas.tseries.offsets import Hour
from sklearn.model_selection import TimeSeriesSplit
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error as mse
from sklearn.model_selection import RandomizedSearchCV
from keras.preprocessing.sequence import TimeseriesGenerator
import xgboost as xgb

np.random.seed(42)


In [2]:

global busses
busses =        ['310_PV_1', '310_PV_2', '320_PV_1', '314_PV_1', '314_PV_2', '313_PV_1', '314_PV_3', '314_PV_4', '313_PV_2', '324_PV_1',    
                 '312_PV_1', '324_PV_2', '324_PV_3', '113_PV_1', '319_PV_1', '215_PV_1', '102_PV_1', '101_PV_1', '102_PV_2',
                 '104_PV_1', '101_PV_2', '101_PV_3', '101_PV_4', '103_PV_1', '119_PV_1']



In [3]:
df = pd.read_csv('PV_deseason_15.csv', parse_dates=[0], index_col=0)

In [4]:
def lags(df, n):
    
    df_new = df
    
    for i in range(n):
        name = "lag "+ str(i+1)
        df_new[name] = df['310_PV_1'].shift(i+1)
    
    return df_new
    

In [5]:
def TrainTest(df):
    
    num_rows = df.shape[0]
    
    num_training = (num_rows * 8)//10
   
    #train = df.iloc[0:num_training]
    #test = df.iloc[num_training:num_rows]
    
    
    return num_training 

In [6]:
def TestModel(X,test, mod):
    
    MSEs = []
    
    for i in range(len(X)):
        
        print(X.iloc[i].to_frame().transpose())
        pred = mod.predict(X.iloc[i].to_frame().transpose())
        #pred = scaler.inverse_transform(pred)
        
        print(pred)
        print(test.iloc[i])
        
        MSEs.append(mse([test.iloc[i]],pred))
    
        
        
    return MSEs

In [7]:



def model1Train(X_train,Y_train,X_test,Y_test):
    
    
    mod = xgb.XGBRegressor()
    
    mod.fit(X_train, Y_train, eval_set = [(X_train, Y_train),(X_test, Y_test)])#keep low for now, edit later eval_set = [(X_train, y_train),(X_test, y_test)]
    
    return mod

    

In [8]:
def model2Train(X_train,Y_train):
    params = {'eta' : [0.001, 0.01, 0.1, 0.25, 0.3, 0.4, 0.5, 0.8],
              'gamma' : [0, 1, 2, 3, 4, 5, 10, 20, 40, 80, 100],
              'max_depth' : [2, 3, 4, 5, 6, 7, 8, 9, 10],
              'min_child_weight' : [0,1, 2, 3, 4, 5, 10, 20, 40, 80, 100],
              'max_delta_step' : [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]         
    }
    
    mod = xgb.XGBRegressor()
    
    rand = RandomizedSearchCV(mod, param_distributions = params, n_iter = 15, n_jobs = -1, verbose = 1, random_state = 7)
    
    rand.fit(X_train, Y_train)#keep low for now, edit later eval_set = [(X_train, y_train),(X_test, y_test)]
    
    params = rand.best_params_
    
    return rand, params

In [9]:
def runModels(df, last):
    scaler = MinMaxScaler()
     
    bound = TrainTest(df)
    
    
    last_index =pd.DatetimeIndex(data = [idx.replace(year = 2019) for idx in last.index])
    df_index = df.index
    new_df_idx = last_index.append(df_index)
    
    array_df = df['310_PV_1'].to_numpy()
    
    array_df = np.append(last['310_PV_1'].to_numpy(), array_df)
    
    
    
    new_df = pd.DataFrame(array_df, columns = ['310_PV_1'])
    new_df['Dates'] = new_df_idx
    new_df = new_df.set_index('Dates')
    

    
    
    lag = lags(new_df, 107)
    
    lag = lag[lag.columns[::-1]]
    

    
    
    lagged_train = lag.iloc[107:bound+107]
    lagged_test = lag.iloc[bound+107:]

    X_train = lagged_train.drop('310_PV_1', axis = 1)
    Y_train = lagged_train['310_PV_1']
    
    X_test = lagged_test.drop('310_PV_1', axis = 1)
    Y_test = lagged_test['310_PV_1']
    
    print(Y_train[1])
    print(Y_test[1])
  
    
    #mod = model1Train(X_train, Y_train,X_test, Y_test)
    mod, params = model2Train(X_train, Y_train)
    
    Tests = TestModel(X_test, Y_test, mod)
    
    print(Tests)
    
    return Tests, params

    

In [10]:

df1 = df[df.index.month.isin([1,2,3])]
df1 = df1.iloc[:-1 , :]
print(df1)
df2 = df[df.index.month.isin([4,5,6])]
df3 = df[df.index.month.isin([7,8,9])]
df4 = df[df.index.month.isin([10,11,12])]

                     320_PV_1  314_PV_1  314_PV_2  313_PV_1  314_PV_3  \
Date                                                                    
2020-01-01 00:15:00  3.966453  3.980737  4.282982  7.276192  6.895283   
2020-01-01 00:30:00  3.966107  3.980367  4.282545  7.275664  6.894732   
2020-01-01 00:45:00  3.965761  3.979998  4.282108  7.275137  6.894181   
2020-01-01 01:00:00  3.965415  3.979628  4.281671  7.274609  6.893630   
2020-01-01 01:15:00  3.965069  3.979259  4.281233  7.274081  6.893079   
...                       ...       ...       ...       ...       ...   
2020-03-31 22:45:00  0.880274  0.763739  0.579910  2.526283  2.095675   
2020-03-31 23:00:00  0.879928  0.763376  0.579482  2.525721  2.095125   
2020-03-31 23:15:00  0.879581  0.763014  0.579053  2.525159  2.094575   
2020-03-31 23:30:00  0.879234  0.762651  0.578625  2.524598  2.094024   
2020-03-31 23:45:00  0.878887  0.762289  0.578196  2.524036  2.093474   

                     314_PV_4  313_PV_2  310_PV_1 

In [11]:
mse1, param1 = runModels(df1,df4.iloc[-107:])

4.125291466810914
1.6454898259911186
Fitting 5 folds for each of 15 candidates, totalling 75 fits


C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['310_PV_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['310_PV_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joinin

                     lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-13 19:15:00 -2.61448 -1.724143  4.739966 -6.519696 -6.418702   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-13 19:15:00 -4.580824 -2.443491 -0.402061  1.296474  1.654844  ...   

                        lag 10      lag 9     lag 8     lag 7     lag 6  \
2020-03-13 19:15:00 -15.331883 -12.029519 -5.359668 -6.317959 -4.866415   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-03-13 19:15:00 -2.831537 -0.714418  0.902427  1.503425  1.641035  

[1 rows x 107 columns]
[0.19646487]
1.6458579469421952
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-13 19:30:00 -1.724143  4.739966 -6.519696 -6.418702 -4.580824   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-13 19:30:00 -2.443491 -0.402061  1.296474  1.654844  1.678515  ...   

                        lag 10     lag 9   

[1.0825254]
1.6410707268167697
                      lag 107   lag 106   lag 105   lag 104  lag 103  \
2020-03-13 22:45:00  1.677571  1.677198  1.676826  1.676453  1.67608   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-13 22:45:00  1.675707  1.675334  1.674961  1.674588  1.674215  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-03-13 22:45:00  1.644385  1.644017  1.643649  1.643281  1.642912   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-03-13 22:45:00  1.642544  1.642176  1.641807  1.641439  1.641071  

[1 rows x 107 columns]
[1.1324643]
1.6407023998955133
                      lag 107   lag 106   lag 105  lag 104   lag 103  \
2020-03-13 23:00:00  1.677198  1.676826  1.676453  1.67608  1.675707   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-13 23:00:00  1.675334  1.674961  1.674588  1.674215  1.673842  ...   

                   

[1.0780914]
1.6359048234988318
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-14 02:15:00  1.672351  1.671978  1.671605  1.673778  1.673411   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-14 02:15:00  1.673044  1.672678  1.672311  1.671944  1.671578  ...   

                       lag 10     lag 9     lag 8     lag 7    lag 6  \
2020-03-14 02:15:00  1.639226  1.638857  1.638488  1.638119  1.63775   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-03-14 02:15:00  1.637381  1.637012  1.636643  1.636274  1.635905  

[1 rows x 107 columns]
[1.0780914]
1.6355357240606505
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-14 02:30:00  1.671978  1.671605  1.673778  1.673411  1.673044   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-14 02:30:00  1.672678  1.672311  1.671944  1.671578  1.671211  ...   

                 

...

[0.7319771]
1.0513691379078391
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-31 05:15:00  1.087109  1.086747  1.086386  1.086025  1.085663   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-31 05:15:00  1.085302  1.084941  1.084579  1.084218  1.083856  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-03-31 05:15:00  1.054581  1.054224  1.053867  1.053511  1.053154   

                        lag 5    lag 4     lag 3     lag 2     lag 1  
2020-03-31 05:15:00  1.052797  1.05244  1.052083  1.051726  1.051369  

[1 rows x 107 columns]
[0.16251032]
0.8174055266894609
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-31 05:30:00  1.086747  1.086386  1.086025  1.085663  1.085302   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-31 05:30:00  1.084941  1.084579  1.084218  1.083856  1.083495  ...   

                

[-11.883673]
-21.033033093651063
                      lag 107   lag 106  lag 105   lag 104   lag 103  \
2020-03-31 09:15:00 -0.591079  3.228505  4.99481  2.153192 -5.403454   

                       lag 102    lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-31 09:15:00 -14.180592 -13.813194  3.500652 -1.208726 -6.012093  ...   

                       lag 10     lag 9     lag 8     lag 7   lag 6     lag 5  \
2020-03-31 09:15:00  6.493679  7.620097  6.980123  4.352443  0.1346 -6.366577   

                         lag 4      lag 3      lag 2      lag 1  
2020-03-31 09:15:00 -13.980322 -14.531499 -14.788687 -21.033033  

[1 rows x 107 columns]
[-19.492702]
-20.724373859738208
                      lag 107  lag 106   lag 105   lag 104    lag 103  \
2020-03-31 09:30:00  3.228505  4.99481  2.153192 -5.403454 -14.180592   

                       lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-31 09:30:00 -13.813194  3.500652 -1.208726 -6.012093 -11.67393  ...   

   

[-20.225044]
-22.613530260986565
                       lag 107    lag 106    lag 105    lag 104   lag 103  \
2020-03-31 13:00:00 -19.564264 -18.223369 -20.003239 -20.278465  2.516802   

                      lag 102   lag 101   lag 100    lag 99   lag 98  ...  \
2020-03-31 13:00:00  3.956877  6.714438 -4.371443  6.908523  4.90898  ...   

                       lag 10      lag 9      lag 8    lag 7     lag 6  \
2020-03-31 13:00:00 -21.46004 -27.476518 -19.939716 -4.96603 -8.824311   

                         lag 5      lag 4      lag 3      lag 2     lag 1  
2020-03-31 13:00:00 -13.768657 -18.562184 -19.601613 -20.544867 -22.61353  

[1 rows x 107 columns]
[-21.604456]
-24.74858726719928
                       lag 107    lag 106    lag 105   lag 104   lag 103  \
2020-03-31 13:15:00 -18.223369 -20.003239 -20.278465  2.516802  3.956877   

                      lag 102   lag 101   lag 100   lag 99    lag 98  ...  \
2020-03-31 13:15:00  6.714438 -4.371443  6.908523  4.90898  5.582389  

[-16.129456]
-15.946848822060744
                     lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-31 17:00:00  5.11027  4.364552  1.848343  0.923391  4.909641   

                      lag 102   lag 101    lag 100    lag 99    lag 98  ...  \
2020-03-31 17:00:00  6.954087  2.220664 -13.394179 -7.124049 -8.930423  ...   

                        lag 10      lag 9      lag 8      lag 7      lag 6  \
2020-03-31 17:00:00 -26.955924 -27.626227 -25.829317 -22.754265 -28.369377   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-03-31 17:00:00 -26.326019 -24.525557 -21.808975 -18.355781 -15.946849  

[1 rows x 107 columns]
[-12.544189]
-12.544474419314486
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-31 17:15:00  4.364552  1.848343  0.923391  4.909641  6.954087   

                      lag 102    lag 101   lag 100    lag 99    lag 98  ...  \
2020-03-31 17:15:00  2.220664 -13.394179 -7.124049 -8.930423 -5.90674

[2.0489593]
1.0292024136631852
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-31 20:45:00 -3.059373 -1.017932  0.680612  1.038993  1.062674   

                      lag 102   lag 101   lag 100   lag 99    lag 98  ...  \
2020-03-31 20:45:00  1.062858  1.062495  1.062133  1.06177  1.061407  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-03-31 20:45:00 -1.329324  0.287531  0.888539  1.026159  1.030993   

                        lag 5     lag 4     lag 3    lag 2     lag 1  
2020-03-31 20:45:00  1.030635  1.030277  1.029919  1.02956  1.029202  

[1 rows x 107 columns]
[1.2778236]
1.0288441517865436
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-03-31 21:00:00 -1.017932  0.680612  1.038993  1.062674  1.062858   

                      lag 102   lag 101  lag 100    lag 99    lag 98  ...  \
2020-03-31 21:00:00  1.062495  1.062133  1.06177  1.061407  1.061044  ...   

                     

In [12]:
mse2, param2 = runModels(df2,df1.iloc[-107:])

C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['310_PV_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['310_PV_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joinin

1.02382432794521
-1.0140342875825024
Fitting 5 folds for each of 15 candidates, totalling 75 fits
                      lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-12 19:00:00  8.061595  10.014964  11.724071  13.526621  14.796656   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-12 19:00:00  14.63855  12.59028  10.29201  8.042647  1.459677  ...   

                       lag 10     lag 9     lag 8     lag 7      lag 6  \
2020-06-12 19:00:00  7.454126  8.384815  9.155668  9.856029  10.420597   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-06-12 19:00:00  9.461396  8.093451  7.441353  1.680238 -1.121587  

[1 rows x 107 columns]
[-0.80430657]
-1.024231101647498
                       lag 107    lag 106    lag 105    lag 104   lag 103  \
2020-06-12 19:15:00  10.014964  11.724071  13.526621  14.796656  14.63855   

                      lag 102   lag 101   lag 100    lag 99   lag 98  ...  \
2020-06-

[-0.7252612]
-1.0164492304024044
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-12 22:45:00 -0.996885 -0.997068 -0.997251 -0.997434 -0.997618   

                      lag 102   lag 101   lag 100   lag 99    lag 98  ...  \
2020-06-12 22:45:00 -0.997801 -0.997984 -0.998167 -0.99835 -0.998533  ...   

                       lag 10     lag 9     lag 8     lag 7    lag 6  \
2020-06-12 22:45:00 -1.014777 -1.014963 -1.015148 -1.015334 -1.01552   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-06-12 22:45:00 -1.015706 -1.015892 -1.016077 -1.016263 -1.016449  

[1 rows x 107 columns]
[-0.7252612]
-1.016635099612456
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-12 23:00:00 -0.997068 -0.997251 -0.997434 -0.997618 -0.997801   

                      lag 102   lag 101  lag 100    lag 99    lag 98  ...  \
2020-06-12 23:00:00 -0.997984 -0.998167 -0.99835 -0.998533 -0.998717  ...   

                  

[-0.71919996]
-1.0188666584438
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-13 02:00:00 -0.999267 -0.999451 -0.999635 -0.999819 -1.000003   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-13 02:00:00 -1.000187 -1.000371 -1.000554 -1.000738 -1.000922  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-06-13 02:00:00 -1.017193 -1.017379 -1.017565 -1.017751 -1.017937   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-06-13 02:00:00 -1.018123 -1.018309 -1.018495 -1.018681 -1.018867  

[1 rows x 107 columns]
[-0.71919996]
-1.019052843665797
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-13 02:15:00 -0.999451 -0.999635 -0.999819 -1.000003 -1.000187   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-13 02:15:00 -1.000371 -1.000554 -1.000738 -1.000922 -1.001106  ...   

             

[-0.40120825]
1.058853430294656
                      lag 107   lag 106  lag 105   lag 104   lag 103  \
2020-06-13 05:30:00 -1.001842 -1.002026 -1.00221 -1.002394 -1.002578   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-13 05:30:00 -1.002763 -1.002947 -1.003131 -1.003315 -1.003499  ...   

                       lag 10     lag 9    lag 8     lag 7     lag 6  \
2020-06-13 05:30:00 -1.019798 -1.019984 -1.02017 -1.020356 -1.020542   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-06-13 05:30:00 -1.020729 -1.020915 -1.021102 -1.021288  1.058853  

[1 rows x 107 columns]
[2.546067]
6.959759903846308
                      lag 107  lag 106   lag 105   lag 104   lag 103  \
2020-06-13 05:45:00 -1.002026 -1.00221 -1.002394 -1.002578 -1.002763   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-13 05:45:00 -1.002947 -1.003131 -1.003315 -1.003499 -0.675541  ...   

                      

...

[-9.507132]
-19.116378047967828
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 08:00:00 -0.169084  5.132763  7.824227  9.077985  6.767537   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 08:00:00 -1.928977  7.308935  9.968978  1.595961 -4.064761  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-06-30 08:00:00  4.493802  6.881165  7.596943 -1.671158 -6.176418   

                        lag 5     lag 4      lag 3      lag 2      lag 1  
2020-06-30 08:00:00 -4.152716 -6.208522 -12.787826 -14.479697 -19.116378  

[1 rows x 107 columns]
[-15.825467]
-20.19212980581717
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 08:15:00  5.132763  7.824227  9.077985  6.767537 -1.928977   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 08:15:00  7.308935  9.968978  1.595961 -4.064761 -4.682314  ...   

       

[-8.904005]
-13.630320159306166
                       lag 107    lag 106    lag 105    lag 104   lag 103  \
2020-06-30 12:00:00 -20.106209 -21.063106 -14.962353 -13.919796 -5.236256   

                       lag 102   lag 101    lag 100    lag 99    lag 98  ...  \
2020-06-30 12:00:00 -10.740421 -7.256607 -15.952849 -9.012205 -9.103528  ...   

                        lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-06-30 12:00:00 -11.097733 -6.778949 -2.901696 -0.949032 -1.406478   

                        lag 5     lag 4     lag 3      lag 2     lag 1  
2020-06-30 12:00:00 -3.806821 -1.595687 -7.639745 -11.307847 -13.63032  

[1 rows x 107 columns]
[-12.238296]
-19.37191911418285
                       lag 107    lag 106    lag 105   lag 104    lag 103  \
2020-06-30 12:15:00 -21.063106 -14.962353 -13.919796 -5.236256 -10.740421   

                      lag 102    lag 101   lag 100    lag 99   lag 98  ...  \
2020-06-30 12:15:00 -7.256607 -15.952849 -9.012205 -9.103528 -8.8142

[-22.760302]
-23.499936432994424
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 15:45:00 -19.392726 -23.171481 -25.720455 -26.213691 -25.714304   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 15:45:00 -23.509179 -22.798317 -21.134996 -19.871128 -19.529119   

                     ...     lag 10      lag 9     lag 8     lag 7      lag 6  \
2020-06-30 15:45:00  ... -21.370352 -17.192006 -14.88825 -17.46892 -12.511066   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-06-30 15:45:00 -19.254304 -25.675958 -28.577393 -24.416534 -23.499936  

[1 rows x 107 columns]
[-22.27189]
-22.02213686209161
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 16:00:00 -23.171481 -25.720455 -26.213691 -25.714304 -23.509179   

                       lag 102    lag 101    lag 100     lag 99    lag 98  \
2020-06-30 16:00:00 -22.798317 -21.134996 -19.8

[-1.5431706]
-1.2125248555423749
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 19:45:00 -1.283959  3.419526  7.928203  6.746715  9.415227   

                     lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 19:45:00  8.36598  5.049793 -0.148909 -1.210998 -1.205873  ...   

                        lag 10     lag 9    lag 8     lag 7     lag 6  \
2020-06-30 19:45:00 -10.176652 -6.945301 -7.33772 -3.938882 -3.290865   

                       lag 5     lag 4     lag 3     lag 2     lag 1  
2020-06-30 19:45:00 -1.81853 -1.320239 -1.222768 -1.212455 -1.212525  

[1 rows x 107 columns]
[-1.1698214]
-1.212594760230612
                      lag 107   lag 106   lag 105   lag 104  lag 103  \
2020-06-30 20:00:00  3.419526  7.928203  6.746715  9.415227  8.36598   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 20:00:00  5.049793 -0.148909 -1.210998 -1.205873 -1.205941  ...   

                  

[-1.0903805]
-1.2135747827767087
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 23:30:00 -1.206277 -1.206344 -1.206411 -1.206479 -1.206546   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 23:30:00 -1.206613 -1.206681 -1.206748 -1.206816 -1.206884  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-06-30 23:30:00 -1.212944 -1.213014 -1.213084 -1.213154 -1.213224   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-06-30 23:30:00 -1.213294 -1.213365 -1.213435 -1.213505 -1.213575  

[1 rows x 107 columns]
[-1.0628341]
-1.213644857078796
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 23:45:00 -1.206344 -1.206411 -1.206479 -1.206546 -1.206613   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 23:45:00 -1.206681 -1.206748 -1.206816 -1.206884 -1.206952  ...   

            

In [13]:
mse3, param3 = runModels(df3,df2.iloc[-107:])

-1.2138554560886252
6.175858867114261
Fitting 5 folds for each of 15 candidates, totalling 75 fits


C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['310_PV_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['310_PV_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joinin

                      lag 107  lag 106  lag 105  lag 104   lag 103   lag 102  \
2020-09-12 14:15:00  5.484291  5.64251  5.59062  6.73791  6.305692  7.246425   

                      lag 101   lag 100    lag 99    lag 98  ...    lag 10  \
2020-09-12 14:15:00  8.183333  8.012317  6.957967  6.721924  ...  5.222557   

                        lag 9     lag 8     lag 7     lag 6     lag 5  \
2020-09-12 14:15:00  6.029688  3.790917  3.548321  4.080315  3.979249   

                        lag 4     lag 3     lag 2     lag 1  
2020-09-12 14:15:00  5.000861  5.118921  4.392718  5.159139  

[1 rows x 107 columns]
[5.5053325]
5.831296524845143
                     lag 107  lag 106  lag 105   lag 104   lag 103   lag 102  \
2020-09-12 14:30:00  5.64251  5.59062  6.73791  6.305692  7.246425  8.183333   

                      lag 101   lag 100    lag 99    lag 98  ...    lag 10  \
2020-09-12 14:30:00  8.012317  6.957967  6.721924  6.442165  ...  6.029688   

                        lag 9     lag 8

[0.64944786]
-0.0054607804154525
                      lag 107  lag 106    lag 105    lag 104   lag 103  \
2020-09-12 18:15:00  8.792025  9.55926  10.411741  10.282528  10.94348   

                       lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-09-12 18:15:00  10.467819  9.932595  9.206934  8.075262  5.413809  ...   

                      lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-09-12 18:15:00  7.87572  8.843506  9.027413  9.314598  8.957521   

                        lag 5     lag 4     lag 3    lag 2     lag 1  
2020-09-12 18:15:00  9.027219  8.564405  7.573448  4.52566 -0.005461  

[1 rows x 107 columns]
[-0.9028274]
-2.387674542238853
                     lag 107    lag 106    lag 105   lag 104    lag 103  \
2020-09-12 18:30:00  9.55926  10.411741  10.282528  10.94348  10.467819   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-09-12 18:30:00  9.932595  9.206934  8.075262  5.413809  2.785142  ...   

        

[-0.22410107]
-0.0214319267314522
                     lag 107   lag 106  lag 105   lag 104  lag 103   lag 102  \
2020-09-12 22:15:00 -0.05571 -0.055414 -0.05512 -0.054825 -0.05453 -0.054235   

                     lag 101   lag 100   lag 99    lag 98  ...    lag 10  \
2020-09-12 22:15:00 -0.05394 -0.053645 -0.05335 -0.053055  ... -0.024128   

                        lag 9     lag 8     lag 7     lag 6    lag 5    lag 4  \
2020-09-12 22:15:00 -0.023828 -0.023528 -0.023229 -0.022929 -0.02263 -0.02233   

                        lag 3     lag 2     lag 1  
2020-09-12 22:15:00 -0.022031 -0.021731 -0.021432  

[1 rows x 107 columns]
[-0.22410107]
-0.021132451538385
                      lag 107  lag 106   lag 105  lag 104   lag 103  lag 102  \
2020-09-12 22:30:00 -0.055414 -0.05512 -0.054825 -0.05453 -0.054235 -0.05394   

                      lag 101  lag 100    lag 99   lag 98  ...    lag 10  \
2020-09-12 22:30:00 -0.053645 -0.05335 -0.053055 -0.05276  ... -0.023828   

              

...

[7.1471357]
9.11467644269415
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-09-30 07:00:00  0.592698  0.593087  0.593476  0.593865  0.341248   

                      lag 102   lag 101  lag 100    lag 99    lag 98  ...  \
2020-09-30 07:00:00 -0.690603 -1.761799  -3.8207 -0.088617  6.323794  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-09-30 07:00:00  0.632994  0.633387  0.633781  0.400568 -0.697127   

                       lag 5     lag 4     lag 3     lag 2     lag 1  
2020-09-30 07:00:00 -1.67187 -3.584318 -1.660974  5.876305  9.114676  

[1 rows x 107 columns]
[10.042947]
9.908512445412017
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-09-30 07:15:00  0.593087  0.593476  0.593865  0.341248 -0.690603   

                      lag 102  lag 101   lag 100    lag 99    lag 98  ...  \
2020-09-30 07:15:00 -1.761799  -3.8207 -0.088617  6.323794  9.310795  ...   

                       l

[2.6400077]
2.5231539281819764
                      lag 107   lag 106  lag 105   lag 104   lag 103  \
2020-09-30 11:00:00  5.220778  5.278817   4.6762  4.248446  3.469327   

                      lag 102  lag 101   lag 100    lag 99   lag 98  ...  \
2020-09-30 11:00:00  2.312885  1.68076  0.826777  0.561865  0.20351  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-09-30 11:00:00  4.861419  3.471648  3.461385  3.437462  3.347691   

                        lag 5    lag 4     lag 3     lag 2     lag 1  
2020-09-30 11:00:00  2.682237  2.69192  2.842586  2.972214  2.523154  

[1 rows x 107 columns]
[2.054646]
2.627372205904596
                      lag 107  lag 106   lag 105   lag 104   lag 103  lag 102  \
2020-09-30 11:15:00  5.278817   4.6762  4.248446  3.469327  2.312885  1.68076   

                      lag 101   lag 100   lag 99    lag 98  ...    lag 10  \
2020-09-30 11:15:00  0.826777  0.561865  0.20351  0.091057  ...  3.471648   

           

[2.5581846]
3.9854511839069495
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-09-30 15:00:00 -0.259345 -0.624803  0.082689  0.819689  0.682099   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-09-30 15:00:00  0.727842  0.291892  0.178892  0.615073  0.136772  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-09-30 15:00:00 -0.673275 -1.007855 -1.208828  0.579543  0.297695   

                        lag 5     lag 4     lag 3    lag 2     lag 1  
2020-09-30 15:00:00 -1.895082 -1.728569  0.510349  2.62167  3.985451  

[1 rows x 107 columns]
[2.9209125]
5.216445020528933
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-09-30 15:15:00 -0.624803  0.082689  0.819689  0.682099  0.727842   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-09-30 15:15:00  0.291892  0.178892  0.615073  0.136772  0.021313  ...   

                  

[-0.5497984]
0.5122248244758527
                     lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-09-30 19:00:00  2.42009  3.114467  2.305566  0.070435 -4.688467   

                      lag 102   lag 101   lag 100   lag 99    lag 98  ...  \
2020-09-30 19:00:00 -7.486713 -5.648074 -3.509981 -1.46779  0.231505  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-09-30 19:00:00  6.027818  4.570833  2.273958 -4.688764 -7.679628   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-09-30 19:00:00 -5.860657 -3.825018 -1.707139 -0.089534  0.512225  

[1 rows x 107 columns]
[0.16020629]
0.650595344254274
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-09-30 19:15:00  3.114467  2.305566  0.070435 -4.688467 -7.486713   

                      lag 102   lag 101  lag 100    lag 99    lag 98  ...  \
2020-09-30 19:15:00 -5.648074 -3.509981 -1.46779  0.231505  0.590637  ...   

                    

[0.3767538]
0.6612782411502582
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-09-30 22:45:00  0.617166  0.617554  0.617941  0.618329  0.618716   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-09-30 22:45:00  0.619104  0.619492  0.619879  0.620267  0.620655  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-09-30 22:45:00  0.657748  0.658141  0.658533  0.658925  0.659317   

                       lag 5     lag 4     lag 3     lag 2     lag 1  
2020-09-30 22:45:00  0.65971  0.660102  0.660494  0.660886  0.661278  

[1 rows x 107 columns]
[0.37181297]
0.6616704128819908
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-09-30 23:00:00  0.617554  0.617941  0.618329  0.618716  0.619104   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-09-30 23:00:00  0.619492  0.619879  0.620267  0.620655  0.621042  ...   

                

In [14]:
mse4, param4 = runModels(df4,df3.iloc[-107:])

C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['310_PV_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['310_PV_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_18440\239345827.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joinin

0.6640192857039633
-3.894053519849813
Fitting 5 folds for each of 15 candidates, totalling 75 fits
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-13 14:15:00  5.600211  6.611574  8.170477  5.252332 -6.833574   

                      lag 102   lag 101  lag 100    lag 99    lag 98  ...  \
2020-12-13 14:15:00  1.508389 -8.473418  4.60789  4.153405  3.957664  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-12-13 14:15:00  7.347088  7.095335  7.876096  6.344015  7.084885   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-12-13 14:15:00  8.555263  8.651051  8.896839  8.294266  7.347977  

[1 rows x 107 columns]
[7.5307593]
-5.615797669258955
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-13 14:30:00  6.611574  8.170477  5.252332 -6.833574  1.508389   

                      lag 102  lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-13 14:30:00 -8.473418

[-1.8777968]
-2.6116541054936944
                      lag 107   lag 106   lag 105  lag 104   lag 103  \
2020-12-13 18:00:00  2.632394  2.716161  1.827796 -1.46494 -7.094288   

                       lag 102    lag 101    lag 100   lag 99    lag 98  ...  \
2020-12-13 18:00:00 -15.794128 -13.396154 -10.624683 -7.59037 -5.125184  ...   

                       lag 10   lag 9     lag 8      lag 7      lag 6  \
2020-12-13 18:00:00  3.098661 -4.7673 -8.914682 -12.810424 -15.649336   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-12-13 18:00:00 -12.62486 -9.259946 -6.652137 -4.450338 -2.611654  

[1 rows x 107 columns]
[-0.63033944]
-0.4735167949509975
                      lag 107   lag 106  lag 105   lag 104    lag 103  \
2020-12-13 18:15:00  2.716161  1.827796 -1.46494 -7.094288 -15.794128   

                       lag 102    lag 101  lag 100    lag 99    lag 98  ...  \
2020-12-13 18:15:00 -13.396154 -10.624683 -7.59037 -5.125184 -3.050434  ...   

      

[3.539283]
3.65614652654792
                     lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-13 21:30:00  3.50239  3.600364  3.611179  3.611612  3.612044   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-13 21:30:00  3.612477  3.612909  3.613342  3.613774  3.614207  ...   

                      lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-12-13 21:30:00  3.65171  3.652689  3.653121  3.653554  3.653986   

                        lag 5    lag 4     lag 3     lag 2     lag 1  
2020-12-13 21:30:00  3.654418  3.65485  3.655282  3.655714  3.656147  

[1 rows x 107 columns]
[3.539283]
3.656578669561679
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-13 21:45:00  3.600364  3.611179  3.611612  3.612044  3.612477   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-13 21:45:00  3.612909  3.613342  3.613774  3.614207  3.614639  ...   

                       lag

[3.545193]
3.665192324145236
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-14 01:15:00  3.616801  3.617234  3.617666  3.618099  3.618531   

                      lag 102   lag 101   lag 100   lag 99    lag 98  ...  \
2020-12-14 01:15:00  3.618963  3.619395  3.619828  3.62026  3.620692  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-12-14 01:15:00  3.658739  3.659171  3.659603  3.660035  3.660467   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-12-14 01:15:00  3.660899  3.663877  3.664316  3.664754  3.665192  

[1 rows x 107 columns]
[3.51563]
3.665630625917869
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-14 01:30:00  3.617234  3.617666  3.618099  3.618531  3.618963   

                      lag 102   lag 101  lag 100    lag 99    lag 98  ...  \
2020-12-14 01:30:00  3.619395  3.619828  3.62026  3.620692  3.621124  ...   

                       l

...

[-8.968814]
-9.12198818996187
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-31 08:00:00  4.086286  2.961044  1.915584 -0.234795 -2.902386   

                      lag 102   lag 101    lag 100     lag 99    lag 98  ...  \
2020-12-31 08:00:00 -5.173803 -7.382925 -10.438222 -12.983682 -7.275044  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-12-31 08:00:00  3.115591  2.044445 -0.014405 -2.615605 -4.803145   

                        lag 5     lag 4      lag 3      lag 2     lag 1  
2020-12-31 08:00:00 -6.816094 -9.815655 -13.289806 -15.678984 -9.121988  

[1 rows x 107 columns]
[-4.5861096]
-3.2537896965281146
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-31 08:15:00  2.961044  1.915584 -0.234795 -2.902386 -5.173803   

                      lag 102    lag 101    lag 100    lag 99    lag 98  ...  \
2020-12-31 08:15:00 -7.382925 -10.438222 -12.983682 -7.275044 -3.644548  ...   

  

[3.7827575]
3.1941554188663908
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-31 11:45:00  1.561208  2.589791  1.344331  0.330291 -0.325279   

                      lag 102   lag 101   lag 100     lag 99    lag 98  ...  \
2020-12-31 11:45:00 -1.805439 -0.129042 -3.095542 -14.483899 -6.494114  ...   

                       lag 10     lag 9    lag 8    lag 7     lag 6     lag 5  \
2020-12-31 11:45:00  5.476273  5.519881  4.42114  3.80054  4.202345  3.877374   

                        lag 4     lag 3     lag 2     lag 1  
2020-12-31 11:45:00  4.064971  3.890546  3.286613  3.194155  

[1 rows x 107 columns]
[2.9893327]
2.3191840609901924
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-31 12:00:00  2.589791  1.344331  0.330291 -0.325279 -1.805439   

                      lag 102   lag 101    lag 100    lag 99    lag 98  ...  \
2020-12-31 12:00:00 -0.129042 -3.095542 -14.483899 -6.494114 -4.361706  ...   

               

[0.8548619]
0.937508674669136
                      lag 107    lag 106  lag 105   lag 104   lag 103  \
2020-12-31 15:45:00  2.331376 -16.653976 -3.07512  0.695812 -1.217682   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-12-31 15:45:00 -19.559318 -15.002047 -15.556524 -22.124117 -15.096081   

                     ...    lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-12-31 15:45:00  ...  3.323181  3.502308  2.433074  2.086791  2.089688   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-12-31 15:45:00  1.744771  1.996029  2.505211  2.158928  0.937509  

[1 rows x 107 columns]
[-2.4559145]
-0.4284458990461584
                       lag 107  lag 106   lag 105   lag 104    lag 103  \
2020-12-31 16:00:00 -16.653976 -3.07512  0.695812 -1.217682 -19.559318   

                       lag 102    lag 101    lag 100     lag 99    lag 98  \
2020-12-31 16:00:00 -15.002047 -15.556524 -22.124117 -15.096081 -13.84564   

    

[3.9381685]
4.424964850021103
                       lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-31 19:30:00 -12.624586 -9.853108 -6.818788 -4.353594 -2.278837   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-31 19:30:00 -0.112823  2.302371  3.775216  4.274016  4.371997  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-12-31 19:30:00 -8.487727 -5.879911 -3.678106 -1.839416  0.298728   

                       lag 5     lag 4     lag 3    lag 2     lag 1  
2020-12-31 19:30:00  2.34097  4.040315  4.399497  4.42398  4.424965  

[1 rows x 107 columns]
[3.932659]
4.425403551042647
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-31 19:45:00 -9.853108 -6.818788 -4.353594 -2.278837 -0.112823   

                      lag 102   lag 101   lag 100    lag 99   lag 98  ...  \
2020-12-31 19:45:00  2.302371  3.775216  4.274016  4.371997  4.38282  ...   

                      

[3.963113]
4.43197996737139
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-31 23:30:00  4.385458  4.385898  4.386338  4.386777  4.387217   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-31 23:30:00  4.387656  4.388096  4.388536  4.388975  4.389415  ...   

                       lag 10     lag 9     lag 8    lag 7     lag 6  \
2020-12-31 23:30:00  4.428035  4.428473  4.428911  4.42935  4.429788   

                        lag 5     lag 4     lag 3     lag 2    lag 1  
2020-12-31 23:30:00  4.430227  4.430665  4.431103  4.431542  4.43198  

[1 rows x 107 columns]
[3.963113]
4.432418297687102
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-12-31 23:45:00  4.385898  4.386338  4.386777  4.387217  4.387656   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-31 23:45:00  4.388096  4.388536  4.388975  4.389415  4.389854  ...   

                       l

In [15]:
print('season 1')

print('model 1:')
print(param1)



season 1
model 1:
{'min_child_weight': 40, 'max_depth': 4, 'max_delta_step': 7, 'gamma': 5, 'eta': 0.1}


In [16]:
print('season 1')

print('model 1:')
print(param2)


season 1
model 1:
{'min_child_weight': 40, 'max_depth': 4, 'max_delta_step': 7, 'gamma': 5, 'eta': 0.1}


In [17]:
print('season 1')

print('model 1:')
print(param3)



season 1
model 1:
{'min_child_weight': 40, 'max_depth': 4, 'max_delta_step': 7, 'gamma': 5, 'eta': 0.1}


In [18]:
print('season 1')

print('model 1:')
print(param4)



season 1
model 1:
{'min_child_weight': 40, 'max_depth': 4, 'max_delta_step': 7, 'gamma': 5, 'eta': 0.1}


In [19]:
d = {'Season 1':mse1,'Season 2':mse2,'Season 3':mse3,'Season 4':mse4}
df_errors_GBDT = pd.DataFrame({k:pd.Series(v) for k,v in d.items()})

df_errors_GBDT.to_csv('GBDT_errors_randomsearch.csv')
